In [ ]:
%matplotlib osx

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
%config InlineBackend.figure_format='retina'
from matplotlib.animation import FFMpegWriter
metadata = dict(title='1246', artist='Matplotlib', comment='yuhhh')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [ ]:
%matplotlib osx
plt.style.use('/Users/bimalrdesai/miniconda3/lib/python3.9/site-packages/matplotlib/mpl-data/stylelib/astrophysics.mplstyle')

In [ ]:
m1246 = 0.87*2e30          
G = 6.67E-11  

mE = 6E24          
mb = 7.0*6e24        
mc = 9.0*6e24        
md = 6.3*6e24        
me = 15*6e24
mbc = 4.3*6e24

ab = 0.049*1.5e11   
ac = 0.061*1.5e11 
ad = 0.131*1.5e11
ae = 0.211*1.5e11
abc = 0.055*1.5e11

day = 60*60*24      
pb = 4.3*day
pc = 5.9*day
pd = 18.7*day
pe = 37.9*day
pbc = 5.04*day

rcm = (mb*ab+md*ad+mc*ac+me*ae+mbc*abc)/(m1246+mb+mc+md+me+mbc)

r1246 = np.array([-rcm, 0])
rb = np.array([ab, 0])
rc = np.array([ac, 0])
rd = np.array([ad, 0])
re = np.array([ae, 0])
rbc = np.array([abc, 0])

w1246 = np.sqrt(G*(m1246+mb)/ab**3)
wb = np.sqrt(G*(m1246+mb)/ab**3)
wc = np.sqrt(G*(m1246+mc)/ac**3)
wd = np.sqrt(G*(m1246+md)/ad**3)
we = np.sqrt(G*(m1246+me)/ae**3)
wbc = np.sqrt(G*(m1246+mbc)/abc**3)

v1246 = np.array([0, r1246[0]*w1246])
vb = np.array([0, rb[0]*wb])
vc = np.array([0, rc[0]*wc])
vd = np.array([0, rd[0]*wd])
ve = np.array([0, re[0]*we])
vbc = np.array([0, rbc[0]*wbc])

y0A = np.concatenate((r1246, v1246))
y0b = np.concatenate((rb, vb))
y0c = np.concatenate((rc, vc))
y0d = np.concatenate((rd, vd))
y0e = np.concatenate((re, ve))
y0bc = np.concatenate((rbc, vbc))

y0 = np.concatenate((y0A, y0b, y0c, y0d, y0e, y0bc))

In [ ]:
def Force(m1, m2, r1, r2):
    global G
    r = np.linalg.norm(r1-r2)
    return -m1*m2*G/r**3 * (r1-r2)
def Force2(m1, m2, m3, m4, m5, r1, r2, r3, r4, r5):
    global G
    rdiff1 = np.linalg.norm(r1-r2)
    rdiff2 = np.linalg.norm(r1-r3)
    rdiff3 = np.linalg.norm(r1-r4)
    rdiff4 = np.linalg.norm(r1-r5)
    f1 = -m1*m2*G/rdiff1**3 * (r1-r2)
    f2 = -m1*m3*G/rdiff2**3 * (r1-r3)
    f3 = -m1*m4*G/rdiff3**3 * (r1-r4)
    f4 = -m1*m5*G/rdiff4**3 * (r1-r5)
    return f1+f2+f3+f4

In [ ]:
def KeplerODE(t, y):
    global G, m1246, mb, mc, md, me, mbc
    r1246 = y[0:2]
    v1246 = y[2:4]
    #rB = y[4:6]
    #vB = y[6:8]
    rb = y[4:6]
    vb = y[6:8]
    rc = y[8:10]
    vc = y[10:12]
    rd = y[12:14]
    vd = y[14:16]
    re = y[16:18]
    ve = y[18:20]
    rbc = y[20:22]
    vbc = y[22:24]
    
    

    dr1246 = v1246
    dv1246 = Force(m1246, mb, r1246, rb)/m1246
    
    drb = vb
    dvb = Force2(mb, m1246, mbc, mc, md, rb, r1246, rbc, rc, rd)/mb

    drc = vc
    dvc = Force2(mc, m1246, mb, mbc, md, rc, r1246, rb, rbc, rd)/mc
    
    drd = vd
    dvd = Force(md, m1246, rd, r1246)/md

    dre = ve
    dve = Force(me, m1246, re, r1246)/me

    drbc = vbc
    dvbc = Force2(mbc, m1246, mb, mc, md, rbc, r1246, rb, rc, rd)/mbc

    return np.concatenate((dr1246, dv1246, drb, dvb, drc, dvc, drd, dvd, dre, dve, drbc, dvbc))

In [ ]:
n = 1000
dt = pe/n #using period of 47c as it has the longest orbitabl period
tmax = pe + 20*day
t = 0
y = y0

###### POSITION ARRAYS ######
x1246, y1246 = [], []

bx, by = [], []
cx, cy = [], []
dx, dy = [], []
ex, ey = [], []
bcx, bcy = [], []

while(t < tmax):
    x1246.append(y[0])
    y1246.append(y[1])
    bx.append(y[4])
    by.append(y[5])
    cx.append(y[8])
    cy.append(y[9])
    dx.append(y[12])
    dy.append(y[13])
    ex.append(y[16])
    ey.append(y[17])
    bcx.append(y[20])
    bcy.append(y[21])
    
    f1 = KeplerODE(t,        y)
    f2 = KeplerODE(t+dt/2.0, y+f1*dt/2.0)
    f3 = KeplerODE(t+dt/2.0, y+f2*dt/2.0)
    f4 = KeplerODE(t+dt    , y+f3*dt    )
    
    y += (f1 + 2.0*f2 + 2.0*f3 + f4) / 6.0 * dt
    t += dt

In [ ]:
fig = plt.figure(figsize = (15., 15.), dpi=200)
fig.clear()
with writer.saving(fig, "animation2.mp4", dpi=200):
    num_elements = len(x1246)
    angle = np.linspace(0, 2*np.pi, 150)
    for i in range (0,num_elements, 2):
        plt.clf()
        #plt.xlim(min(cx)-AU/2, max(cx)+AU/2)
        #plt.ylim(min(cy)-AU/2, max(cy)+AU/2)
        plt.gca().set_aspect('equal')
        plt.title("TOI-1246")
        plt.xlabel("distance (m)")
        plt.ylabel("distance (m)")
        
        #plot the planets and stars
        #plt.plot(x1246[0:i+1], y1246[0:i+1], '-', color = 'lightcoral', linewidth = 0.5, label='1246')
        #plt.plot(Bx[0:i+1], By[0:i+1], '-r', linewidth = 0.5, label='47B')
        plt.plot(bx[0:i+1], by[0:i+1], '-', color= 'lightcoral') #, label='1246b')
        plt.plot(cx[0:i+1], cy[0:i+1], '-', color = 'lightcoral') #, label='1246c')
        plt.plot(dx[0:i+1], dy[0:i+1], '-', color ='lightcoral') #, label='1246d')
        plt.plot(ex[0:i+1], ey[0:i+1], '-', color = 'lightcoral') #, label='1246e')
        plt.plot(bcx[0:i+1], bcy[0:i+1], '-', color = 'blue')

        plt.plot(x1246[i], y1246[i], '*', color = 'gold', label='1246', markersize=9)
        plt.plot(bx[i], by[i], 'o', color = 'black', markersize=6, label = 'Existing Planets')
        plt.plot(cx[i], cy[i], 'o', color = 'black', markersize=5)
        plt.plot(dx[i], dy[i], 'o', color = 'black', markersize=7)
        plt.plot(ex[i], ey[i], 'o', color = 'black', markersize=7.4)
        plt.plot(bcx[i], bcy[i], 'o', color = 'blue', markersize=6, label = 'Inserted Planet')

        plt.xlim(-4e10, 4e10)
        plt.ylim(-4e10, 4e10)
        #plt.plot(0,0,'+k', markersize=2)
        plt.legend(loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.05)
        writer.grab_frame()
    for i in range(5):
        writer.grab_frame() #powerpoint keeps cutting off my animations so i needed to grab extra frames